In [1]:
# import os
# os.environ['CUDA_VISIBLE_DEVICES'] = '1'

# !pip install --upgrade segmentation_models_pytorch

In [2]:
import os
import shutil
import pathlib
import gc
import pandas as pd
import ttach as tta
from pathlib import Path
from PIL import Image
import numpy as np
import cv2 as cv
import random
import matplotlib.pyplot as plt
# from tqdm.auto import tqdm
from tqdm.notebook import tqdm
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch import optim
import torch
from torch.utils.data import DataLoader, random_split
from torch.utils.data import Dataset
from torch.optim.swa_utils import AveragedModel, SWALR

import torchvision
from torchvision import datasets
import cv2
from torch.cuda import amp

import torchvision.transforms as T
from torchvision.transforms import Compose, ToTensor, Resize
from torchvision.utils import make_grid
import optuna

import albumentations as A
from albumentations.pytorch import ToTensorV2
import segmentation_models_pytorch as smp
import timm

In [3]:
def seed_everything(seed=42):
    '''Sets the seed of the entire notebook so results are the same every time we run.
    This is for REPRODUCIBILITY.'''
    np.random.seed(seed)
    random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    os.environ['PYTHONHASHSEED'] = str(seed)

In [4]:
seed_everything(42)

In [5]:
ensemple_type = "No" #"No" #"mine"

In [6]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


In [7]:
import torchvision.transforms as T


class ContrailDataset:
    def __init__(self, df, transform=None, normalize=False):
        self.df = df  
        self.images = df['image']
        self.labels = df['label']
        self.transform =transform
        self.normalize_image = T.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))
        self.normalize=normalize
        
        
    def __len__(self):
        return len(self.images)
        
    def __getitem__(self, idx):
        image = np.load("../../input/" + self.images[idx]).astype(float)   
        label = np.load("../../input/" + self.labels[idx]).astype(float)
        

        # label_cls = 1 if label.sum() > 0 else 0
        if self.transform :
            data = self.transform(image=image, mask=label)
            image  = data['image']
            label  = data['mask']
            image = np.transpose(image, (2, 0, 1))
            label = np.transpose(label, (2, 0, 1))    
            
            
#         return torch.tensor(image), torch.tensor(label)
    
        if self.normalize:
            image = self.normalize_image(torch.tensor(image))
            return image, torch.tensor(label)
        else:
            return torch.tensor(image), torch.tensor(label)
    
    

In [8]:
###TImmunetplusplus model Nirjhar

n_blocks = 4

class TimmSegModel(nn.Module):
    def __init__(self, cfg, segtype='unet', pretrained=True):
        super(TimmSegModel, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 3, stride=1, padding=1, bias=False)
        self.conv2 = nn.Conv2d(6, 12, 3, stride=1, padding=1, bias=False)
        self.conv3 = nn.Conv2d(12, 36, 3, stride=1, padding=1, bias=False)
        self.mybn1 = nn.BatchNorm2d(6)
        self.mybn2 = nn.BatchNorm2d(12)
        self.mybn3 = nn.BatchNorm2d(36)     
        self.encoder = timm.create_model(
            cfg['backbone'],
            in_chans=3,
            features_only=True,
            drop_rate=0.8,
            drop_path_rate=0.5,
            pretrained=False
        )
        self.encoder.conv_stem=nn.Conv2d(6, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)

        self.encoder.blocks[5] = nn.Identity()
        self.encoder.blocks[6] = nn.Sequential(
            nn.Conv2d(self.encoder.blocks[4][2].conv_pwl.out_channels, 320, 1),
            nn.BatchNorm2d(320),
            nn.ReLU6(),
        )
        tr = torch.randn(1,6,64,64)
        g = self.encoder(tr)
        encoder_channels = [1] + [_.shape[1] for _ in g]
        decoder_channels = [256, 128, 64, 32, 16]
        if segtype == 'unet':
            self.decoder = smp.decoders.unetplusplus.decoder.UnetPlusPlusDecoder(
                encoder_channels=encoder_channels[:n_blocks+1],
                decoder_channels=decoder_channels[:n_blocks],
                n_blocks=n_blocks,
            )

        self.segmentation_head = nn.Conv2d(
            decoder_channels[n_blocks-1],
            cfg["num_classes"], 
            kernel_size=(3, 3),
            stride=(1, 1), 
            padding=(1, 1)
        )

    def forward(self,x):
        x = F.relu6(self.mybn1(self.conv1(x)))
        global_features = [0] + self.encoder(x)[:n_blocks]
        seg_features = self.decoder(*global_features)
        seg_features = self.segmentation_head(seg_features)
        return seg_features
    

def load_model1(cfg):
    model = TimmSegModel(cfg)
    model.load_state_dict(torch.load(cfg['model_pth']))
    return model


#### Model 2 Nirjhar

n_blocks =4
class TimmSegModel2(nn.Module):
    def __init__(self, cfg, segtype='unet', pretrained=True):
        super(TimmSegModel2, self).__init__()

        self.encoder = timm.create_model(
            cfg['backbone'],
            in_chans=3,
            features_only=True,
            drop_rate=0.5,
            pretrained=False
        )
        g = self.encoder(torch.rand(1, 3, 128, 128))
        encoder_channels = [1] + [_.shape[1] for _ in g]
        decoder_channels = [256, 128, 64, 32, 16]
        if segtype == 'unet':
            self.decoder = smp.decoders.unetplusplus.decoder.UnetPlusPlusDecoder(
                encoder_channels=encoder_channels[:n_blocks+1],
                decoder_channels=decoder_channels[:n_blocks],
                n_blocks=n_blocks,
            )

        self.segmentation_head = nn.Sequential(
            nn.Conv2d(decoder_channels[n_blocks-1], 1, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1)),
            nn.UpsamplingBilinear2d(scale_factor=1))

    def forward(self,x):
        global_features = [0] + self.encoder(x)[:n_blocks]
        seg_features = self.decoder(*global_features)
        seg_features = self.segmentation_head(seg_features)
        return seg_features
    

def load_model2(cfg):
    model = TimmSegModel2(cfg)
    model.load_state_dict(torch.load(cfg['model_pth']))
    return model


##################

n_blocks = 4

class TimmSegModel3(nn.Module):
    def __init__(self, cfg, segtype='unet', pretrained=True):
        super(TimmSegModel3, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 3, stride=1, padding=1, bias=False)
        self.conv2 = nn.Conv2d(6, 12, 3, stride=1, padding=1, bias=False)
        self.conv3 = nn.Conv2d(12, 36, 3, stride=1, padding=1, bias=False)
        self.mybn1 = nn.BatchNorm2d(6)
        self.mybn2 = nn.BatchNorm2d(12)
        self.mybn3 = nn.BatchNorm2d(36)     
        self.encoder = timm.create_model(
            cfg["backbone"],
            in_chans=3,
            features_only=True,
            drop_rate=0.8,
            drop_path_rate=0.5,
            pretrained=False
        )
        self.encoder.conv_stem=nn.Conv2d(6, 72, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)

        self.encoder.blocks[5] = nn.Identity()
        self.encoder.blocks[6] = nn.Sequential(
            nn.Conv2d(self.encoder.blocks[4][2].conv_pwl.out_channels, 320, 1),
            nn.BatchNorm2d(320),
            nn.ReLU6(),
        )
        tr = torch.randn(1,6,64,64)
        g = self.encoder(tr)
        encoder_channels = [1] + [_.shape[1] for _ in g]
        decoder_channels = [256, 128, 64, 32, 16]
        if segtype == 'unet':
            self.decoder = smp.decoders.unetplusplus.decoder.UnetPlusPlusDecoder(
                encoder_channels=encoder_channels[:n_blocks+1],
                decoder_channels=decoder_channels[:n_blocks],
                n_blocks=n_blocks,
            )

        self.segmentation_head = nn.Conv2d(decoder_channels[n_blocks-1], cfg['num_classes'], kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))

    def forward(self,x):
        x = F.relu6(self.mybn1(self.conv1(x)))
        global_features = [0] + self.encoder(x)[:n_blocks]
        seg_features = self.decoder(*global_features)
        seg_features = self.segmentation_head(seg_features)
        return seg_features
    
    
    
def load_model3(cfg):
    model = TimmSegModel3(cfg)
    model.load_state_dict(torch.load(cfg['model_pth']))
    return model



class TimmSegModel4(nn.Module):
    def __init__(self, cfg, segtype='unet', pretrained=True):
        super(TimmSegModel4, self).__init__()

        self.encoder = timm.create_model(
            cfg["backbone"],
            in_chans=3,
            features_only=True,
            drop_rate=0.5,
            pretrained=False
        )
        g = self.encoder(torch.rand(1, 3, 512, 512))
        encoder_channels = [1] + [_.shape[1] for _ in g]
        decoder_channels = [256, 128, 64, 32, 16]
        if segtype == 'unet':
            self.decoder = smp.decoders.unetplusplus.decoder.UnetPlusPlusDecoder(
                encoder_channels=encoder_channels[:n_blocks+1],
                decoder_channels=decoder_channels[:n_blocks],
                n_blocks=n_blocks,
            )

        self.segmentation_head = nn.Sequential(
            nn.Conv2d(decoder_channels[n_blocks-1], 1, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1)),
            nn.UpsamplingBilinear2d(scale_factor=1))

    def forward(self,x):
        global_features = [0] + self.encoder(x)[:n_blocks]
        seg_features = self.decoder(*global_features)
        seg_features = self.segmentation_head(seg_features)
        return seg_features
    
    
def load_model4(cfg):
    model = TimmSegModel4(cfg)
    model.load_state_dict(torch.load(cfg['model_pth']))
    return model







## Rohit Model 
class Net_R(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.cfg = cfg
        
        self.model = smp.Unet(
            encoder_name=cfg["backbone"],     
            encoder_weights=None,   
            in_channels=3,  
            classes=cfg["num_classes"],
            activation=None
        )
        
    
    def forward(self, inputs):
        mask = self.model(inputs)
        return mask
    
    
def load_modelr1(cfg):
    model = Net_R(cfg)
    model = torch.nn.DataParallel(model).cuda()
    model.load_state_dict(torch.load(cfg['model_pth'], map_location=torch.device('cpu'))['model'])
    return model


def load_modelr1(cfg):
    model = Net_R(cfg)
    model = torch.nn.DataParallel(model).cuda()
    model.load_state_dict(torch.load(cfg['model_pth'], map_location=torch.device('cpu'))['model'])
    return model


# def load_modelr3(cfg):
# #     weight = f"{cfg.architecture.pretrained_weights}"
#     model = Net_R(cfg)
#     model = torch.nn.DataParallel(model).cuda()
    
#     d =  torch.load(cfg['model_pth'], map_location="cpu")
#     if "model" in d:
#         model_weights = d["model"]
#     else:
#         model_weights = d
#     try:
#         model.load_state_dict(model_weights, strict=True)
#     except Exception as e:
#         print("removing unused pretrained layers")
#         for layer_name in re.findall("size mismatch for (.*?):", str(e)):
#             model_weights.pop(layer_name, None)
#         model.load_state_dict(model_weights, strict=False)

#     print(f"Weights loaded from: {cfg.architecture.pretrained_weights}")



#     if idx in [11, 12]:
#         model = TimmSegModelR1(cfg)
#         model = torch.nn.DataParallel(model).cuda()
#         model.load_state_dict(torch.load(cfg['model_pth'], map_location=torch.device('cpu'))['model'])
#     else:
#         model = Net(cfg)    
#         model = torch.nn.DataParallel(model).cuda()
#         model.load_state_dict(torch.load(cfg['model_pth'], map_location=torch.device('cpu'))['model'])

class TimmSegModelR1(nn.Module):
    def __init__(self, cfg, segtype='unet', pretrained=True):
        super(TimmSegModelR1, self).__init__()

        self.n_blocks = 4
        self.encoder = timm.create_model(
            cfg['backbone'],
            in_chans=3,
            features_only=True,
            drop_rate=0.5,
            pretrained=False
        )
        g = self.encoder(torch.rand(1, 3, 128, 128))
        encoder_channels = [1] + [_.shape[1] for _ in g]
        decoder_channels = [256, 128, 64, 32, 16]
        if segtype == 'unet':
            self.decoder = smp.decoders.unetplusplus.decoder.UnetPlusPlusDecoder(
                encoder_channels=encoder_channels[:self.n_blocks+1],
                decoder_channels=decoder_channels[:self.n_blocks],
                n_blocks=self.n_blocks,
            )

        self.segmentation_head = nn.Sequential(
            nn.Conv2d(decoder_channels[self.n_blocks-1], 
                      cfg['num_classes'],
                      kernel_size=(3, 3),
                      stride=(1, 1),
                      padding=(1, 1)
            ),
            nn.UpsamplingBilinear2d(scale_factor=1)
        )

    def forward(self,x):
        global_features = [0] + self.encoder(x)[:self.n_blocks]
        seg_features = self.decoder(*global_features)
        seg_features = self.segmentation_head(seg_features)
        return seg_features


    
def load_modelr2(cfg):
    model = TimmSegModelR1(cfg)
    model = torch.nn.DataParallel(model).cuda()
    model.load_state_dict(torch.load(cfg['model_pth'], map_location=torch.device('cpu'))['model'])
    return model

### Ioannis

In [9]:
# !pip install pytorch-lightning

In [10]:
# from segmentation_models_pytorch.decoders.unet.decoder import UnetDecoder, DecoderBlock
# import torch.nn.functional as F
# import torchvision.transforms as T
# import pickle 
# import glob
# import pytorch_lightning as pl
# import timm 

# print(f"Pytorch version: {torch.__version__}")
# print(f"Segmentation Models version: {smp.__version__}")
# print(f"Timm version: {timm.__version__}")

    
    
# # class args:
# #     size=512 
# #     exp_name = "exp28"
# #     use_folds = [0]
# #     ##use_folds = [0,1,2,3]
# #     in_chans = 3 #12 # 6 # 65
# #     size = 512 #384 # 224
# #     image_size = size
# #     target_size = 1
# #     batch_size = 8 #32
# #     backbone = 'gluon_senet154'
# #     seg_model = "Unet"   ## "Unet++", "MAnet", "Linknet", "FPN", "PSPNet", "PAN", "DeepLabV3",  "DeepLabV3+"
# #     model_name = f'{seg_model}-{backbone}'
# #     pretrained = False
# #     deepsupervision=False 
    
    
# ##########################################################
# class SmpUnetDecoder(nn.Module):
#     def __init__(self,in_channel,skip_channel,out_channel):
#         super().__init__()
#         self.center = nn.Identity()
#         i_channel = [in_channel,]+ out_channel[:-1]
#         s_channel = skip_channel
#         o_channel = out_channel
#         block = [
#             DecoderBlock(i, s, o, use_batchnorm=True, attention_type=None)
#             for i, s, o in zip(i_channel, s_channel, o_channel)
#         ]
#         self.block = nn.ModuleList(block)
        
#     def forward(self, feature, skip):
#         d = self.center(feature)
#         decode = []
#         for i, block in enumerate(self.block):
#             s = skip[i]
#             d = block(d, s)
#             decode.append(d)
#         last  = d
#         return last, decode


# def conv3x3(in_channel, out_channel): #not change resolusion
#     return nn.Conv2d(in_channel,out_channel,
#                       kernel_size=3,stride=1,padding=1,dilation=1,bias=False)

# def conv1x1(in_channel, out_channel): #not change resolution
#     return nn.Conv2d(in_channel,out_channel,
#                       kernel_size=1,stride=1,padding=0,dilation=1,bias=False)
    
# class Net(nn.Module):
#     def __init__(self, cfg, vb=False):
#         super().__init__()
#         self.cfg = cfg
#         self.vb = vb
#         self.crop_depth = None #cfg.crop_depth
#         self.deepsupervision = False #cfg.deepsupervision #True
        
#         # if cfg.backbone == 'resnet34' or cfg.backbone == 'seresnet34':
#         if 'resnet34' in cfg.backbone:
#             conv_dim=64
#             encoder_dim = [conv_dim, 64, 128, 256, 512, ]
#             decoder_dim = [256, 128, 64, 32, 16]
#         else:
#             conv_dim=128 #128
#             encoder_dim  = [conv_dim] + [256, 512, 1024, 2048]
#             decoder_dim = [512, 256, 128, 64, 16]
            
#         # self.encoder = resnet34d(pretrained=False,in_chans=CFG.one_depth)
#         self.encoder = timm.create_model(cfg.backbone, pretrained=cfg.pretrained, in_chans=cfg.in_chans, num_classes=0) #drop_path_rate=0.2, 
#         self.decoder = SmpUnetDecoder(
#             in_channel=encoder_dim[-1],
#             skip_channel=encoder_dim[:-1][::-1] + [0],
#             out_channel=decoder_dim
#         )
#         ### seg head
#         seg_head_in_c = 16 #if 'resnet34' in cfg.backbone else 128
#         self.logit = nn.Conv2d(decoder_dim[-1], 1, kernel_size=1)
        
#         #-- pool attention weight
#         self.weight = nn.ModuleList([
#             nn.Conv2d(encoder_dim[i], 1, kernel_size=1, padding=0) for i in range(len(encoder_dim))
#         ])
#         #### deep supervision
#         deep_ch = [16, 64, 128, 256]   # [64, 64, 64, 64]
#         self.deep4 = conv1x1(deep_ch[0],1)#.apply(init_weight)
#         self.deep3 = conv1x1(deep_ch[1],1)#.apply(init_weight)
#         self.deep2 = conv1x1(deep_ch[2],1)#.apply(init_weight)
#         self.deep1 = conv1x1(deep_ch[3],1)#.apply(init_weight)
        
#         self.up1 = nn.Upsample(scale_factor=8, mode='bilinear', align_corners=True)
#         self.up2 = nn.Upsample(scale_factor=4, mode='bilinear', align_corners=True)
#         self.up3 = nn.Upsample(scale_factor=2, mode='bilinear', align_corners=True)
#         self.up4 = nn.Upsample(scale_factor=1, mode='bilinear', align_corners=True)
        
#     def forward(self, batch):
#         K = 1
#         x = batch
#         # ----
#         encoder = []
#         e = self.encoder
        
#         x = e.conv1(x)
#         x = e.bn1(x)
#         x = e.act1(x)
#         encoder.append(x)
        
#         x = F.avg_pool2d(x,kernel_size=2,stride=2)
#         x = e.layer1(x)
#         encoder.append(x)
        
#         x = e.layer2(x)
#         encoder.append(x)
        
#         x = e.layer3(x)
#         encoder.append(x)
        
#         x = e.layer4(x)
#         encoder.append(x)
#         #if self.vb: print('encoder', [f.shape for f in encoder])

#         ### decoder
#         last, decoder = self.decoder(feature=encoder[-1], skip = encoder[:-1][::-1] + [None])
#         #if self.vb: print('decoder',[f.shape for f in decoder])
#         #if self.vb: print('last',last.shape)
        
#         ### head
#         logit = self.logit(last)
#         #if self.vb: print('logit',logit.shape)
        
#         if self.deepsupervision:
#             y4 = decoder[-1]  ### torch.Size([B, 16, 256, 256])
#             y3 = decoder[-2]  ### torch.Size([B, 32, 128, 128])
#             y2 = decoder[-3]  ### torch.Size([B, 64, 64, 64])
#             y1 = decoder[-4]  ### torch.Size([B, 128, 32, 32])
#             ### --> B x C x H x W
#             y1 = self.up1(y1)  ### x 8
#             y2 = self.up2(y2)  ### x 4 
#             y3 = self.up3(y3)  ### x 2
#             y4 = self.up4(y4)  ### x 1  
#             ##################
#             s4 = self.deep4(y4) ### --> B x 1 x H x W
#             s3 = self.deep3(y3)
#             s2 = self.deep2(y2)
#             s1 = self.deep1(y1)
#             logits_deeps = [s4,s3,s2,s1]
#             #if self.vb: print('logits_deeps', s1.shape,  s2.shape,  s3.shape,  s4.shape)
#             return logit, logits_deeps
#         return logit

In [11]:
# class args:
#     size=512 
#     exp_name = "exp28"
#     use_folds = [0]
#     ##use_folds = [0,1,2,3]
#     in_chans = 3 #12 # 6 # 65
#     size = 512 #384 # 224
#     image_size = size
#     target_size = 1
#     batch_size = 8 #32
#     backbone = 'gluon_senet154'
#     seg_model = "Unet"   ## "Unet++", "MAnet", "Linknet", "FPN", "PSPNet", "PAN", "DeepLabV3",  "DeepLabV3+"
#     model_name = f'{seg_model}-{backbone}'
#     pretrained = False
#     deepsupervision=False 

In [12]:
# class LightningModule(pl.LightningModule):
#     def __init__(self):
#         super().__init__()
#         self.model = Net(args) 

#     def forward(self, batch):
#         return self.model(batch)

    
# def load_model_exp28(cfg):
#     model = LightningModule().load_from_checkpoint(cfg['model_pth']) 
#     return model



# ### ensemble muiltiple checkpoints 


# ### move all weights to nb 
# MODEL_DIR_EXP28 = "/kaggle/input/contrails-exp28b-senet154-512/"    
# CKPTS_EXP28 = [
#     #     ######## 4-skf split 
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0.ckpt',
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v1.ckpt',
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v2.ckpt',
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v3.ckpt',
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v4.ckpt',
#     #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v5.ckpt'
#     #     ####### full train.csv 
#     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1.ckpt',
#     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1-v1.ckpt',
#     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1-v2.ckpt',
# ]


# class EnsembleModel(nn.Module):
#     def __init__(self, cfg):
#         super().__init__()
#         self.model = nn.ModuleList()
        
#         #for fold, w in zip(use_folds, weights):
#         for i, model_path in enumerate(cfg['model_pth']):
            
#             #model_path = CKPTS_EXP28[i]
#             _model = LightningModule().load_from_checkpoint(model_path) #cfg['model_pth']
#             _model.eval()
#             print('Load weights from:', model_path)

#             self.model.append(_model)
#             #self.weights.append(w)
        
    
#     def forward(self, x):
#         outputs=[]
#         for m in self.model:
#             outputs.append(m(x)) #(torch.sigmoid(out))
#         res = torch.stack(outputs,dim=0).mean(0)
#         return res  

# def load_model_exp28_snapshot(cfg):
#     model = EnsembleModel(cfg)
#     return model

In [13]:
### -----------------------------------------
### exp28 Senet154 + deep_supervision 
### -----------------------------------------

import warnings 
warnings.filterwarnings('ignore')
# from einops import rearrange, reduce, repeat
from segmentation_models_pytorch.decoders.unet.decoder import UnetDecoder, DecoderBlock
import torch.nn.functional as F
import torchvision.transforms as T
import pickle 
import glob
import pytorch_lightning as pl
import timm 

print(f"Pytorch version: {torch.__version__}")
print(f"Segmentation Models version: {smp.__version__}")
print(f"Timm version: {timm.__version__}")


#################################
##### Dataset 
################################


class DatasetExp28(torch.utils.data.Dataset):
    def __init__(self, df, image_size=256, train=True, normalize=True):
        
        self.df = df
        self.trn = train
        self.df_idx: pd.DataFrame = pd.DataFrame({'idx': os.listdir(f'/kaggle/input/google-research-identify-contrails-reduce-global-warming/test')})
        self.normalize_image = T.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))
        self.image_size = image_size
        self.normalize = normalize
        if image_size != 256:
            self.resize_image = T.transforms.Resize(image_size)
        
        #self.images = df['image']
    
    def read_record(self, directory):
        record_data = {}
        for x in [
            "band_11", 
            "band_14", 
            "band_15"
        ]:

            record_data[x] = np.load(os.path.join(directory, x + ".npy"))

        return record_data

    def normalize_range(self, data, bounds):
        """Maps data to the range [0, 1]."""
        return (data - bounds[0]) / (bounds[1] - bounds[0])
    
    def get_false_color(self, record_data):
        _T11_BOUNDS = (243, 303)
        _CLOUD_TOP_TDIFF_BOUNDS = (-4, 5)
        _TDIFF_BOUNDS = (-4, 2)
        
        N_TIMES_BEFORE = 4

        r = self.normalize_range(record_data["band_15"] - record_data["band_14"], _TDIFF_BOUNDS)
        g = self.normalize_range(record_data["band_14"] - record_data["band_11"], _CLOUD_TOP_TDIFF_BOUNDS)
        b = self.normalize_range(record_data["band_14"], _T11_BOUNDS)
        false_color = np.clip(np.stack([r, g, b], axis=2), 0, 1)
        img = false_color[..., N_TIMES_BEFORE]

        return img
    
    def __len__(self):
        return len(self.df)
    
    def __getitem__(self, index):
        row = self.df.iloc[index]
        con_path = row.path
        data = self.read_record(con_path)
        img = self.get_false_color(data)
        
        ###### Rohit dataset -- todo 
        #img = np.load(self.images[index]).astype(float)
        
        img = torch.tensor(np.reshape(img, (256, 256, 3))).to(torch.float32).permute(2, 0, 1)
        
        if self.image_size != 256:
            img = self.resize_image(img)
            
        if self.normalize:
            img = self.normalize_image(img)
        
        #image_id = int(self.df_idx.iloc[index]['idx'])
        return img.float() #, torch.tensor(image_id)
    

    
#############################    
### MODEL    
#############################
class SmpUnetDecoder(nn.Module):
    def __init__(self,in_channel,skip_channel,out_channel):
        super().__init__()
        self.center = nn.Identity()
        i_channel = [in_channel,]+ out_channel[:-1]
        s_channel = skip_channel
        o_channel = out_channel
        block = [
            DecoderBlock(i, s, o, use_batchnorm=True, attention_type=None)
            for i, s, o in zip(i_channel, s_channel, o_channel)
        ]
        self.block = nn.ModuleList(block)
        
    def forward(self, feature, skip):
        d = self.center(feature)
        decode = []
        for i, block in enumerate(self.block):
            s = skip[i]
            d = block(d, s)
            decode.append(d)
        last  = d
        return last, decode


def conv3x3(in_channel, out_channel): #not change resolusion
    return nn.Conv2d(in_channel,out_channel,
                      kernel_size=3,stride=1,padding=1,dilation=1,bias=False)

def conv1x1(in_channel, out_channel): #not change resolution
    return nn.Conv2d(in_channel,out_channel,
                      kernel_size=1,stride=1,padding=0,dilation=1,bias=False)
    
class Net(nn.Module):
    def __init__(self, cfg, vb=False):
        super().__init__()
        self.cfg = cfg
        self.vb = vb
        self.crop_depth = None #cfg.crop_depth
        self.deepsupervision = False #cfg.deepsupervision #True
        
        # if cfg.backbone == 'resnet34' or cfg.backbone == 'seresnet34':
        if 'resnet34' in cfg.backbone:
            conv_dim=64
            encoder_dim = [conv_dim, 64, 128, 256, 512, ]
            decoder_dim = [256, 128, 64, 32, 16]
        else:
            conv_dim=128 #128
            encoder_dim  = [conv_dim] + [256, 512, 1024, 2048]
            decoder_dim = [512, 256, 128, 64, 16]
            
        # self.encoder = resnet34d(pretrained=False,in_chans=CFG.one_depth)
        self.encoder = timm.create_model(cfg.backbone, pretrained=cfg.pretrained, in_chans=cfg.in_chans, num_classes=0) #drop_path_rate=0.2, 
        self.decoder = SmpUnetDecoder(
            in_channel=encoder_dim[-1],
            skip_channel=encoder_dim[:-1][::-1] + [0],
            out_channel=decoder_dim
        )
        ### seg head
        seg_head_in_c = 16 #if 'resnet34' in cfg.backbone else 128
        self.logit = nn.Conv2d(decoder_dim[-1], 1, kernel_size=1)
        
        #-- pool attention weight
        self.weight = nn.ModuleList([
            nn.Conv2d(encoder_dim[i], 1, kernel_size=1, padding=0) for i in range(len(encoder_dim))
        ])
        #### deep supervision
        deep_ch = [16, 64, 128, 256]   # [64, 64, 64, 64]
        self.deep4 = conv1x1(deep_ch[0],1)#.apply(init_weight)
        self.deep3 = conv1x1(deep_ch[1],1)#.apply(init_weight)
        self.deep2 = conv1x1(deep_ch[2],1)#.apply(init_weight)
        self.deep1 = conv1x1(deep_ch[3],1)#.apply(init_weight)
        
        self.up1 = nn.Upsample(scale_factor=8, mode='bilinear', align_corners=True)
        self.up2 = nn.Upsample(scale_factor=4, mode='bilinear', align_corners=True)
        self.up3 = nn.Upsample(scale_factor=2, mode='bilinear', align_corners=True)
        self.up4 = nn.Upsample(scale_factor=1, mode='bilinear', align_corners=True)
        
    def forward(self, batch):
        K = 1
        x = batch
        # ----
        encoder = []
        e = self.encoder
        
        x = e.conv1(x)
        x = e.bn1(x)
        x = e.act1(x)
        encoder.append(x)
        
        x = F.avg_pool2d(x,kernel_size=2,stride=2)
        x = e.layer1(x)
        encoder.append(x)
        
        x = e.layer2(x)
        encoder.append(x)
        
        x = e.layer3(x)
        encoder.append(x)
        
        x = e.layer4(x)
        encoder.append(x)
        #if self.vb: print('encoder', [f.shape for f in encoder])

        ### decoder
        last, decoder = self.decoder(feature=encoder[-1], skip = encoder[:-1][::-1] + [None])
        #if self.vb: print('decoder',[f.shape for f in decoder])
        #if self.vb: print('last',last.shape)
        
        ### head
        logit = self.logit(last)
        #if self.vb: print('logit',logit.shape)
        
        if self.deepsupervision:
            y4 = decoder[-1]  ### torch.Size([B, 16, 256, 256])
            y3 = decoder[-2]  ### torch.Size([B, 32, 128, 128])
            y2 = decoder[-3]  ### torch.Size([B, 64, 64, 64])
            y1 = decoder[-4]  ### torch.Size([B, 128, 32, 32])
            ### --> B x C x H x W
            y1 = self.up1(y1)  ### x 8
            y2 = self.up2(y2)  ### x 4 
            y3 = self.up3(y3)  ### x 2
            y4 = self.up4(y4)  ### x 1  
            ##################
            s4 = self.deep4(y4) ### --> B x 1 x H x W
            s3 = self.deep3(y3)
            s2 = self.deep2(y2)
            s1 = self.deep1(y1)
            logits_deeps = [s4,s3,s2,s1]
            #if self.vb: print('logits_deeps', s1.shape,  s2.shape,  s3.shape,  s4.shape)
            return logit, logits_deeps
        return logit

    
class args_28:
    size=512 
    exp_name = "exp28"
    use_folds = [0]
    ##use_folds = [0,1,2,3]
    in_chans = 3 #12 # 6 # 65
    size = 512 #384 # 224
    image_size = size
    target_size = 1
    batch_size = 8 #32
    backbone = 'gluon_senet154'
    seg_model = "Unet"   ## "Unet++", "MAnet", "Linknet", "FPN", "PSPNet", "PAN", "DeepLabV3",  "DeepLabV3+"
    model_name = f'{seg_model}-{backbone}'
    pretrained = False
    deepsupervision=False 

    
    
class LightningModule_28(pl.LightningModule):
    def __init__(self):
        super().__init__()
        self.model = Net(args_28) 

    def forward(self, batch):
        return self.model(batch)

    
def load_model_exp28(cfg):
    model = LightningModule_28().load_from_checkpoint(cfg['model_pth']) 
    return model



### ensemble muiltiple checkpoints 


### move all weights to nb 
MODEL_DIR_EXP28 = "/kaggle/input/contrails-exp28b-senet154-512/"    
CKPTS_EXP28 = [
    #     ######## 4-skf split 
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0.ckpt',
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v1.ckpt',
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v2.ckpt',
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v3.ckpt',
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v4.ckpt',
    #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v5.ckpt'
    #     ####### full train.csv 
    '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1.ckpt',
    '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1-v1.ckpt',
    '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold-1-v2.ckpt',
]


class EnsembleModel_28(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.model = nn.ModuleList()
        
        for i, model_path in enumerate(cfg['model_pth']):
            _model = LightningModule_28().load_from_checkpoint(model_path) #cfg['model_pth']
            _model.eval()
            print('Load weights from:', model_path)
            self.model.append(_model)        
    
    def forward(self, x):
        outputs=[]
        for m in self.model:
            outputs.append(m(x)) #(torch.sigmoid(out))
        res = torch.stack(outputs,dim=0).mean(0)
        return res  

def load_model_exp28_snapshot(cfg):
    model = EnsembleModel_28(cfg)
    return model

Pytorch version: 2.0.1+cu117
Segmentation Models version: 0.3.3
Timm version: 0.9.2


In [14]:
### -----------------------------------------
### exp27
### -----------------------------------------


class args_27:
    in_chans = 3 
    size = 512 #384 # 224
    backbone = 'resnest26d'
    seg_model = "Unet"   ## "Unet++", "MAnet", "Linknet", "FPN", "PSPNet", "PAN", "DeepLabV3",  "DeepLabV3+"
    pretrained = False
    deepsupervision=False 



class SmpUnetDecoder(nn.Module):
    def __init__(self,in_channel,skip_channel,out_channel):
        super().__init__()
        self.center = nn.Identity()
        i_channel = [in_channel,]+ out_channel[:-1]
        s_channel = skip_channel
        o_channel = out_channel
        block = [
            DecoderBlock(i, s, o, use_batchnorm=True, attention_type=None)
            for i, s, o in zip(i_channel, s_channel, o_channel)
        ]
        self.block = nn.ModuleList(block)
        
    def forward(self, feature, skip):
        d = self.center(feature)
        decode = []
        for i, block in enumerate(self.block):
            s = skip[i]
            d = block(d, s)
            decode.append(d)
        last  = d
        return last, decode


def conv3x3(in_channel, out_channel): #not change resolusion
    return nn.Conv2d(in_channel,out_channel,
                      kernel_size=3,stride=1,padding=1,dilation=1,bias=False)

def conv1x1(in_channel, out_channel): #not change resolution
    return nn.Conv2d(in_channel,out_channel,
                      kernel_size=1,stride=1,padding=0,dilation=1,bias=False)
    
class Net_27(nn.Module):
    def __init__(self, cfg, vb=False):
        super().__init__()
        self.cfg = cfg
        self.vb = vb
        self.crop_depth = None #cfg.crop_depth
        self.deepsupervision = False #cfg.deepsupervision #True
        
        # if cfg.backbone == 'resnet34' or cfg.backbone == 'seresnet34':
        if 'resnet34' in cfg.backbone:
            conv_dim=64
            encoder_dim = [conv_dim, 64, 128, 256, 512, ]
            decoder_dim = [256, 128, 64, 32, 16]
        else:
            conv_dim=64 #128
            encoder_dim  = [conv_dim] + [256, 512, 1024, 2048]
            decoder_dim = [256, 128, 64, 32, 16]
            
        # self.encoder = resnet34d(pretrained=False,in_chans=CFG.one_depth)
        self.encoder = timm.create_model(cfg.backbone, pretrained=False, in_chans=3, num_classes=0) #drop_path_rate=0.2, 
        self.decoder = SmpUnetDecoder(
            in_channel=encoder_dim[-1],
            skip_channel=encoder_dim[:-1][::-1] + [0],
            out_channel=decoder_dim
        )
        ### seg head
        seg_head_in_c = 16 #if 'resnet34' in cfg.backbone else 128
        self.logit = nn.Conv2d(decoder_dim[-1], 1, kernel_size=1)
        
        #-- pool attention weight
        self.weight = nn.ModuleList([
            nn.Conv2d(encoder_dim[i], 1, kernel_size=1, padding=0) for i in range(len(encoder_dim))
        ])
        #### deep supervision
        deep_ch = [16, 32, 64, 128] # [64, 64, 64, 64]
        self.deep4 = conv1x1(deep_ch[0],1)#.apply(init_weight)
        self.deep3 = conv1x1(deep_ch[1],1)#.apply(init_weight)
        self.deep2 = conv1x1(deep_ch[2],1)#.apply(init_weight)
        self.deep1 = conv1x1(deep_ch[3],1)#.apply(init_weight)
        
        self.up1 = nn.Upsample(scale_factor=8, mode='bilinear', align_corners=True)
        self.up2 = nn.Upsample(scale_factor=4, mode='bilinear', align_corners=True)
        self.up3 = nn.Upsample(scale_factor=2, mode='bilinear', align_corners=True)
        self.up4 = nn.Upsample(scale_factor=1, mode='bilinear', align_corners=True)
        
    def forward(self, batch):
        K = 1
        x = batch
        # ----
        encoder = []
        e = self.encoder
        
        x = e.conv1(x)
        x = e.bn1(x)
        x = e.act1(x)
        encoder.append(x)
        
        x = F.avg_pool2d(x,kernel_size=2,stride=2)
        x = e.layer1(x)
        encoder.append(x)
        
        x = e.layer2(x)
        encoder.append(x)
        
        x = e.layer3(x)
        encoder.append(x)
        
        x = e.layer4(x)
        encoder.append(x)
        #if self.vb: print('encoder', [f.shape for f in encoder])

        ### decoder
        last, decoder = self.decoder(feature=encoder[-1], skip = encoder[:-1][::-1] + [None])
        #if self.vb: print('decoder',[f.shape for f in decoder])
        #if self.vb: print('last',last.shape)
        
        ### head
        logit = self.logit(last)
        #if self.vb: print('logit',logit.shape)
        
        if self.deepsupervision:
            y4 = decoder[-1]  ### torch.Size([B, 16, 256, 256])
            y3 = decoder[-2]  ### torch.Size([B, 32, 128, 128])
            y2 = decoder[-3]  ### torch.Size([B, 64, 64, 64])
            y1 = decoder[-4]  ### torch.Size([B, 128, 32, 32])
            ### --> B x C x H x W
            y1 = self.up1(y1)  ### x 8
            y2 = self.up2(y2)  ### x 4 
            y3 = self.up3(y3)  ### x 2
            y4 = self.up4(y4)  ### x 1  
            ##################
            s4 = self.deep4(y4) ### --> B x 1 x H x W
            s3 = self.deep3(y3)
            s2 = self.deep2(y2)
            s1 = self.deep1(y1)
            logits_deeps = [s4,s3,s2,s1]
            #if self.vb: print('logits_deeps', s1.shape,  s2.shape,  s3.shape,  s4.shape)
            return logit, logits_deeps
        return logit


    
    
class LightningModule_27(pl.LightningModule):
    def __init__(self):
        super().__init__()
        self.model = Net_27(args_27) 

    def forward(self, batch):
        return self.model(batch)

    
class EnsembleModel_27(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.model = nn.ModuleList()
        
        #for fold, w in zip(use_folds, weights):
        for i, model_path in enumerate(cfg['model_pth']):
            
            #model_path = CKPTS_EXP28[i]
            _model = LightningModule_27().load_from_checkpoint(model_path) #cfg['model_pth']
            _model.eval()
            print('Load weights from:', model_path)

            self.model.append(_model)
            #self.weights.append(w)
        
    
    def forward(self, x):
        outputs=[]
        for m in self.model:
            outputs.append(m(x)) #(torch.sigmoid(out))
        res = torch.stack(outputs,dim=0).mean(0)
        return res  

def load_model_exp27_soup(cfg):
    model = EnsembleModel_27(cfg)
    return model

In [15]:
### -----------------------------------------
### exp26 Unet++ regnetx_080
### -----------------------------------------

# class args:
#     backbone = 'timm-regnetx_080'

class SegModel_26(nn.Module):
    def __init__(self):
        super(SegModel_26, self).__init__()
        
        self.seg = smp.UnetPlusPlus(encoder_name='timm-regnetx_080', encoder_weights=None, classes=1, activation=None)
        ##self.seg = seg_models[cfg.seg_model](encoder_name=cfg.backbone, encoder_weights="imagenet", classes=1, activation=None)

    def forward(self,x):
        global_features = self.seg.encoder(x)
        seg_features = self.seg.decoder(*global_features)
        seg_features = self.seg.segmentation_head(seg_features)
        return seg_features
    
    
class LightningModule_26(pl.LightningModule):
    def __init__(self):
        super().__init__()
        self.model = SegModel_26()

    def forward(self, batch):
        return self.model(batch)


class EnsembleModel_26(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.model = nn.ModuleList()
        
        for i, model_path in enumerate(cfg['model_pth']):
            _model = LightningModule_26().load_from_checkpoint(model_path) #cfg['model_pth']
            _model.eval()
            print('Load weights from:', model_path)
            self.model.append(_model)
            #self.weights.append(w)
        
    def forward(self, x):
        outputs=[]
        for m in self.model:
            outputs.append(m(x)) #(torch.sigmoid(out))
        res = torch.stack(outputs,dim=0).mean(0)
        return res  

    
def load_model_exp26_soup(cfg):
    model = EnsembleModel_26(cfg)
    return model

In [16]:
### -----------------------------------------
### exp19 Unet++
### -----------------------------------------

# class args:
#     exp_name = "exp19"
#     in_chans = 3 #12 # 6 # 65
#     size = 256  
#     target_size = 1
#     batch_size = 32
#     backbone = 'timm-resnest26d'


class SegModel_19(nn.Module):
    def __init__(self):
        super(SegModel_19, self).__init__()
        self.seg = smp.UnetPlusPlus(encoder_name='timm-resnest26d', encoder_weights=None, classes=1, activation=None)
    
    def forward(self,x):
        global_features = self.seg.encoder(x)
        seg_features = self.seg.decoder(*global_features)
        seg_features = self.seg.segmentation_head(seg_features)
        return seg_features


class LightningModule_19(pl.LightningModule):
    def __init__(self):
        super().__init__()
        self.model = SegModel_19()

    def forward(self, batch):
        return self.model(batch)

    
class EnsembleModel_19(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.model = nn.ModuleList()
        
        for i, model_path in enumerate(cfg['model_pth']):
            _model = LightningModule_19().load_from_checkpoint(model_path) #cfg['model_pth']
            _model.eval()
            print('Load weights from:', model_path)
            self.model.append(_model)
            #self.weights.append(w)
        
    def forward(self, x):
        outputs=[]
        for m in self.model:
            outputs.append(m(x)) #(torch.sigmoid(out))
        res = torch.stack(outputs,dim=0).mean(0)
        return res  

    
def load_model_exp19_soup(cfg):
    model = EnsembleModel_19(cfg)
    return model

In [17]:
def dice_coef(y_true, y_pred, thr=0.5, epsilon=1e-6):
    y_true = y_true.to(torch.float32)
    y_pred = (y_pred>thr).to(torch.float32)
    inter = (y_true*y_pred).sum()
    den = y_true.sum() + y_pred.sum()
    dice = ((2*inter+epsilon)/(den+epsilon)).mean()
    
    return dice


def get_transform(img_size):
    transform = A.Compose([
        A.Resize(*img_size, interpolation=cv2.INTER_NEAREST),
    ], p=1.0)
    return transform

def get_transform2(img_size):
    transform = A.Compose([
        A.Resize(*img_size, interpolation=cv2.INTER_LINEAR),
    ], p=1.0)
    return transform




In [18]:
val_df = pd.read_csv("../../input/data_utils/val_df_filled.csv")
val_df_full = val_df.copy()

val_dups = np.load("../../input/data_utils/dups_val.npy")

val_dups = [int(val_id) for val_id in val_dups]

In [19]:
# val_df = val_df.loc[~val_df['id'].isin(val_dups)].reset_index(drop=True)
print(val_df.shape, val_df_full.shape)

(1856, 4) (1856, 4)


In [20]:
import re 

def load_modelr3(cfg):
    model = Net_R(cfg)
    model = torch.nn.DataParallel(model).cuda()
#     model_state_dict = model.state_dict()
#     model_state_dict = {k.replace('module.', ''): v for k, v in model_state_dict.items()}
#     model.state_dict = model_state_dict
    
    
#     model_state_dict = ['model']
    
    model.load_state_dict(torch.load(cfg['model_pth'], map_location="cpu")['model']) 
    
#     model.load_state_dict(torch.load(cfg['model_pth'])["model"])

    
    return model



# def load_modelr3(cfg):
# #     weight = f"{cfg.architecture.pretrained_weights}"
    
# #     if cfg.dataset.fold != -1:
# #        weight += f"/checkpoint_dice_ctrl_fold{cfg.dataset.fold}.pth" 
    
#     model = Net_R(cfg)
#     model = torch.nn.DataParallel(model).cuda()
#     model = AveragedModel(model, device="cuda", use_buffers=True)
    
#     model_state_dict = model.state_dict()
#     del model_state_dict['n_averaged']
    
#     for k, v in model_state_dict.items():
#         print(k)
#         print(k.replace('module.module.', 'module.'))
        
    
    
#     model_state_dict = {k.replace('module.', ''): v for k, v in model_state_dict.items()}
    
#     weight = cfg['model_pth']
#     d = torch.load(weight, map_location="cpu")['model']
#     model.load_state_dict(d, strict=True)

    
    

# #     if "model" in d:
# #         model_weights = d["model"]
# #     else:
# #         model_weights = d
# #     try:
# #         model.load_state_dict(model_weights, strict=True)
# #     except Exception as e:
# #         print("removing unused pretrained layers")
# #         for layer_name in re.findall("size mismatch for (.*?):", str(e)):
# #             model_weights.pop(layer_name, None)
# #         model.load_state_dict(model_weights, strict=False)

# #     print(f"Weights loaded from: {cfg['model_pth']}")
    
#     return model
    


In [21]:
CFGS1 = [
    {
        'model_name': 'Unet',
        'backbone': 'efficientnet-b7',
        'img_size': [256, 256],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/efficientnet-b7-256/checkpoint_dice_fold0.pth',
        'threshold': 0.24, #0.24,
        'call_sign': "roh_01_tta",
        'model_func': load_modelr1,
        'tta': True,
        'normalize': False
    }, 
    {
        'model_name': 'Unet',
        'backbone': 'maxvit_small_tf_512',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/maxvitfold0mix_maxvit_small_tf_512_best_epochstage2oof685cv657-00.bin',
        'threshold': 0.62, #0.24,
        'call_sign': "nir_01_tta",
        'model_func': load_model4,
        'tta': True,
        'normalize': False
    },
    
    
    {
        'model_name': 'Unet',
        'backbone': 'eca_nfnet_l1',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl1v2fold0_eca_nfnet_l1_best_epochstage2-00.bin',
        'threshold': 0.62, #0.24,
        'call_sign': "nir_02_tta",
        'model_func': load_model2,
        'tta': True,
        'normalize': False
    },
    {
        'model_name': 'Unet++',
        'backbone': 'tf_efficientnet_b8',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/effb8modelv2fold0_tf_efficientnet_b8_best_epochstage2-00.bin',
        'threshold': 0.79,
        'call_sign': "nir_03_tta", 
        'model_func': load_model3,
        'tta': True,
        'normalize': False
    },
    {
        'model_name': 'Unet++',
        'backbone': 'tf_efficientnet_b7_ns',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/contrail_01/output/nirjhar/qishentrialv2fpn512_tf_efficientnet_b7_ns_best_epochcv650lb675-00.bin',
        'threshold': 0.62, #0.24,
        'call_sign': "nir_04_tta", 
        'model_func': load_model1,
        'tta': True,
        'normalize': False
    }, 
    

#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "ioa_01",
#         'model_func': load_model_exp28_snapshot,
#         'tta': True, #True
#         'normalize': True,
#         'model_pth': [
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_28/Unet-gluon_senet154_fold-1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_28/Unet-gluon_senet154_fold-1-v1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_28/Unet-gluon_senet154_fold-1-v2.ckpt',
#         ]
#     }, 
    
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'model_func': load_model_exp28,
#         'model_pth': '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_28/Unet-gluon_senet154_fold0.ckpt',        
#         'call_sign': "ioa_02",
#         'tta': True, #False, #True
#         'normalize': True
#     }, 
    
    
    {
        'model_name': 'Unet',
        'backbone': 'efficientnet-b7',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output1/exp_10_s2/Unet/efficientnet-b7-512/checkpoint_dice_ctrl_fold0.pth',
        'threshold': 0.24, #0.24,
        'call_sign': "roh_02_tta",
        'model_func': load_modelr1,
        'tta': True,
        'normalize': False
    }, 
    
    {
        'model_name': 'Unet',
        'backbone': 'efficientnet-b7',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output1/exp_10/Unet/efficientnet-b7-512/checkpoint_dice_ctrl_fold0.pth',
        'threshold': 0.24, #0.24,
        'call_sign': "roh_03_tta",
        'model_func': load_modelr1,
        'tta': True,
        'normalize': False
    }, 
    
    {
        'model_name': 'Unet',
        'backbone': 'efficientnet-b7',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output1/exp_10_s2_swa/Unet/efficientnet-b7-512/checkpoint_dice_ctrl_fold0.pth',
        'threshold': 0.24, #0.24,
        'call_sign': "roh_04_tta",
        'model_func': load_modelr1,
        'tta': True,
        'normalize': False
    }, 
    

    {
        'model_name': 'Unet++',
        'backbone': 'tf_efficientnet_b8',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/fullfinetune-effb8modelv2fold0_tf_efficientnet_b8_best_epochstage2cv670-00.bin',
        'threshold': 0.79,
        'call_sign': "nir_05_tta", 
        'model_func': load_model3,
        'tta': True,
        'normalize': False
    },
    {
        'model_name': 'Unet++',
        'backbone': 'tf_efficientnet_b8',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ema_ema-effb8modelv2fold0_tf_efficientnet_b8_best_epochstage2-00.bin',
        'threshold': 0.79,
        'call_sign': "nir_06_tta", 
        'model_func': load_model3,
        'tta': False,
        'normalize': False
    },
    
#     {
#         'model_name': 'Unet++',
#         'backbone': 'eca_nfnet_l1',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/ecal1fulltrain_eca_nfnet_l1_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_07_tta", 
#         'model_func': load_model2,
#         'tta': False,
#         'normalize': False
#     },
    
    
    {
        'model_name': 'Unet',
        'backbone': 'efficientnet-b7',
        'img_size': [512, 512],
        'num_classes': 1,
        'model_pth':  '/home/rohits/pv1/Contrail_Detection/output1/exp_10_s4_swa/Unet/efficientnet-b7-512/checkpoint_dice_ctrl_fold0.pth',
        'threshold': 0.24, #0.24,
        'call_sign': "roh_05_tta",
        'model_func': load_modelr3,
        'tta': False,
        'normalize': False
    }, 
    
    
    
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'eca_nfnet_l0',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output1/exp_10_01/Unet/eca_nfnet_l0-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_05_tta",
#         'model_func': load_modelr2,
#         'tta': True,
#         'normalize': False
#     }, 
    
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'timm-regnetx_080',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'model_func': load_model_exp26_soup,
#         'model_pth': [
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_26/Unetpp-timm-regnetx_080_fold2.ckpt'
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_27/Unet-resnest26d_fold0.ckpt',
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_27/Unet-resnest26d_fold0-v1.ckpt',
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_27/Unet-resnest26d_fold0-v2.ckpt'
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_19/Unetpp-timm-resnest26d_fold0_642.ckpt',
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_19/Unetpp-timm-resnest26d_fold1.ckpt',
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_19/Unetpp-timm-resnest26d_fold2.ckpt',
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/exp_19/Unetpp-timm-resnest26d_fold3.ckpt'
  
        
#         ],
#         'call_sign': "ioa_03",
#         'tta': False, #False, #True
#         'normalize': True
#     }, 
    
    
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "ioa_01",
#         'model_func': load_model_exp28_snapshot,
#         'tta': True, #True
#         'normalize': True,
#         'model_pth': [
# #             ######## full train.csv 
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v2.ckpt',
# #             ######### 4-skf split 
# #             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold0.ckpt',

#         ]
#     }, 
    
]

In [22]:
# # val_df = val_df.head(100)
# def load_checkpoint(cfg, model):
#     weight = f"{cfg.architecture.pretrained_weights}"
    
    
#     d =  torch.load(weight, map_location="cpu")
#     if "model" in d:
#         model_weights = d["model"]
#     else:
#         model_weights = d
#     try:
#         model.load_state_dict(model_weights, strict=True)
#     except Exception as e:
#         print("removing unused pretrained layers")
#         for layer_name in re.findall("size mismatch for (.*?):", str(e)):
#             model_weights.pop(layer_name, None)
#         model.load_state_dict(model_weights, strict=False)

#     print(f"Weights loaded from: {cfg.architecture.pretrained_weights}")

In [23]:
final_preds1 = []

for idx, cfg in enumerate(CFGS1):   

    if idx <= 9:
        continue
        
    print(cfg)
    val_transform = get_transform(cfg['img_size'])
    val_transform2 = get_transform2(cfg['img_size'])

    valid_dataset = ContrailDataset(val_df, transform=val_transform, normalize=False)  
    if cfg['normalize'] and ("ioa_" in cfg['call_sign']):
        valid_dataset = ContrailDataset(val_df, transform=val_transform2, normalize=True)  
#         valid_dataset = ContrailDataset(val_df, transform=val_transform, normalize=True)  


    
    valid_loader = DataLoader(
        valid_dataset, 
        batch_size = 32, #32, 
        shuffle = False, 
        num_workers = 2, 
        pin_memory = True, 
        drop_last = False
    )
    
    
    model = cfg['model_func'](cfg)        
      
    if cfg['tta']:
        if "roh_" in cfg['call_sign']:
            model = tta.SegmentationTTAWrapper(model, tta.aliases.flip_transform(), merge_mode='mean')
        else:
            model = tta.SegmentationTTAWrapper(model, tta.aliases.hflip_transform(), merge_mode='mean')
    
    model.to(device)
    model.eval()
    
    
#     model_base.to(device)
#     model_base.eval()
    
    
    preds = []
    masks_ = []      
        
    for index, (images, masks) in enumerate(tqdm(valid_loader)):  
        images  = images.to(device, dtype=torch.float)
        masks  = masks.to(device, dtype=torch.float)
        if cfg['img_size'][0] != 256:
#             masks = torch.nn.functional.interpolate(masks, size=256, mode='nearest') 
            masks = torch.nn.functional.interpolate(masks, size=256, mode='nearest') 


        masks_.append(torch.squeeze(masks, dim=1))
        with torch.inference_mode():
            images = torch.nn.functional.interpolate(images, size=cfg['img_size'][0], mode='nearest')
            pred = model(images).sigmoid()   
            if cfg['tta']:
                pred = model(images).sigmoid()
#                 pred2 = model(images).sigmoid()
#                 pred = (pred + pred2) / 2
                
            pred = torch.nn.functional.interpolate(pred, size=256, mode='nearest')
            preds.append(torch.squeeze(pred, dim=1))
        
            
            
    model_masks = torch.cat(masks_, dim=0)
    model_preds = torch.cat(preds, dim=0)
        
    print(model)
    print(model_preds.shape)
        
#     model_masks = torch.flatten(model_masks, start_dim=0, end_dim=1)
#     model_preds = torch.flatten(model_preds, start_dim=0, end_dim=1)  
    
    # save
#     torch.save(model_preds, f"../../output/final_preds/{cfg['call_sign']}.pt")    
#     torch.save(model_preds, f"../../output/final_preds/{cfg['call_sign']}_full.pt")    

#     if idx == 6:
#     torch.save(model_masks, f'../../output/final_preds/val_masks.pt')

    np.save(f"../../output/final_preds/{cfg['call_sign']}", model_preds.detach().cpu().numpy())
    if idx == 0:
        np.save(f"../../output/final_preds/val_masks", model_masks.detach().cpu().numpy())

    
    best_threshold = 0.0
    best_dice_score = 0.0
    for threshold in [i / 100 for i in range(101)] :
        score = dice_coef(model_masks, model_preds, thr=threshold).cpu().detach().numpy() 

        
        if score > best_dice_score:
            best_dice_score = score
            best_threshold = threshold
    
        
    print(best_dice_score, best_threshold)
    final_preds1.append(model_preds)
    
    if cfg['tta']: del model
    del model
    torch.cuda.empty_cache()
    gc.collect()

{'model_name': 'Unet', 'backbone': 'efficientnet-b7', 'img_size': [512, 512], 'num_classes': 1, 'model_pth': '/home/rohits/pv1/Contrail_Detection/output1/exp_10_s4_swa/Unet/efficientnet-b7-512/checkpoint_dice_ctrl_fold0.pth', 'threshold': 0.24, 'call_sign': 'roh_05_tta', 'model_func': <function load_modelr3 at 0x7f989dd568c0>, 'tta': False, 'normalize': False}


  0%|          | 0/58 [00:00<?, ?it/s]

DataParallel(
  (module): Net_R(
    (model): Unet(
      (encoder): EfficientNetEncoder(
        (_conv_stem): Conv2dStaticSamePadding(
          3, 64, kernel_size=(3, 3), stride=(2, 2), bias=False
          (static_padding): ZeroPad2d((0, 1, 0, 1))
        )
        (_bn0): BatchNorm2d(64, eps=0.001, momentum=0.010000000000000009, affine=True, track_running_stats=True)
        (_blocks): ModuleList(
          (0): MBConvBlock(
            (_depthwise_conv): Conv2dStaticSamePadding(
              64, 64, kernel_size=(3, 3), stride=[1, 1], groups=64, bias=False
              (static_padding): ZeroPad2d((1, 1, 1, 1))
            )
            (_bn1): BatchNorm2d(64, eps=0.001, momentum=0.010000000000000009, affine=True, track_running_stats=True)
            (_se_reduce): Conv2dStaticSamePadding(
              64, 16, kernel_size=(1, 1), stride=(1, 1)
              (static_padding): Identity()
            )
            (_se_expand): Conv2dStaticSamePadding(
              16, 64, kernel_

0.6723466 0.42


In [47]:
torch.load(CFGS1[10]['model_pth'], map_location="cpu")

{'model': {'model.encoder._conv_stem.weight': tensor([[[[-3.1996e-01, -5.6981e-01, -1.4818e-01],
            [ 8.1577e-02, -3.7720e-01, -1.4447e-02],
            [ 1.8844e-01, -4.6681e-02,  1.0421e-01]],
  
           [[-1.1533e-01, -2.3538e-01,  9.4198e-02],
            [-9.6137e-02, -3.2581e-01,  1.8240e-01],
            [ 1.0208e-01,  2.4413e-02,  1.4392e-01]],
  
           [[-4.0255e-02, -1.8887e-01, -8.8529e-02],
            [-1.7673e-01, -3.5112e-01, -1.8650e-01],
            [-1.1946e-01, -1.2485e-01, -9.6760e-02]]],
  
  
          [[[ 2.4614e-01,  6.6501e-01, -2.9380e-02],
            [-3.1873e-01, -5.9307e-01, -5.9999e-02],
            [ 9.0680e-02, -8.9021e-02,  1.0280e-01]],
  
           [[ 1.0188e+00,  1.6483e+00,  1.2965e-01],
            [-1.2113e+00, -1.6788e+00, -1.1505e-01],
            [ 1.0717e-01,  5.2681e-02,  1.5934e-01]],
  
           [[ 3.7264e-01,  4.7100e-01,  7.0167e-02],
            [-3.2403e-01, -4.2481e-01, -2.1563e-01],
            [-2.6252e-02, -7.11

In [48]:
torch.load(CFGS1[0]['model_pth'], map_location="cpu")

{'model': OrderedDict([('module.model.encoder._conv_stem.weight',
               tensor([[[[-4.1809e-01, -4.6458e-01, -4.7670e-02],
                         [ 4.3236e-02, -2.5923e-01,  7.8750e-02],
                         [ 3.7404e-02, -6.0546e-02,  8.6510e-02]],
               
                        [[-2.4046e-01, -1.1421e-01,  1.9205e-01],
                         [-1.7027e-01, -3.7454e-01,  1.4937e-01],
                         [ 3.1392e-02,  4.6278e-02,  1.8357e-01]],
               
                        [[-1.7292e-01, -3.3625e-01, -1.3655e-01],
                         [-1.1065e-01, -3.1491e-01, -1.7033e-01],
                         [-8.5680e-02, -2.1993e-03,  8.1189e-03]]],
               
               
                       [[[ 3.0160e-01,  6.5580e-01, -2.1357e-02],
                         [-2.8938e-01, -6.2106e-01, -2.6443e-02],
                         [ 5.7303e-02, -1.0481e-01,  1.8726e-02]],
               
                        [[ 1.2676e+00,  1.8713e+00,  6.72

In [54]:
call_signs1 = [
#     "roh_01_tta", # can be removed
    "roh_02_tta",
    
    
#     "roh_03_tta",
    "roh_04_tta", 
    
    
    "nir_01_tta",
#     "nir_02_tta",
#     "nir_03_tta",
#     "nir_04_tta",
#     "nir_05_tta", # remove this from ensemble
    "nir_06_tta",
#     "nir_07_tta",
#     "roh_05_tta",
    
#     "exp32_Unet-tf_efficientnet_b8_soup_preds_0.6663",
    
    "121", 
    "122", 
    "125", 
    "127", 
    "131"  
] 

model_masks = torch.from_numpy(np.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/val_masks.npy")).flatten() 

preds = []

for idx, sign in tqdm(enumerate(call_signs1), total=len(call_signs1)):
    wt = torch.from_numpy(np.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/{sign}.npy")).flatten()   
    preds.append(wt)
    print(wt.shape)
    
    score = dice_coef(model_masks, wt, thr=0.5).cpu().detach().numpy() 
    print(score)
    
    
# # preds1.append(preds2)
    
final_preds = preds
final_preds = torch.stack(final_preds).mean(dim=0)
score = dice_coef(model_masks, final_preds, thr=0.5).cpu().detach().numpy() 

print("0.5 TH Score: ", score)


best_threshold = 0.0
best_dice_score = 0.0
for threshold in [i / 100 for i in range(101)] :
    if threshold < 0.35 or threshold > 0.51:
        continue
    
    score = dice_coef(model_masks, final_preds, thr=threshold).cpu().detach().numpy() 
    if score > best_dice_score:
        best_dice_score = score
        best_threshold = threshold
        
print(best_dice_score, best_threshold)

  0%|          | 0/9 [00:00<?, ?it/s]

torch.Size([121634816])
0.67922837
torch.Size([121634816])
0.6797982
torch.Size([121634816])
0.6567023
torch.Size([121634816])
0.67292583
torch.Size([121634816])
0.6707117
torch.Size([121634816])
0.67332405
torch.Size([121634816])
0.65260977
torch.Size([121634816])
0.6755674
torch.Size([121634816])
0.6600541
0.5 TH Score:  0.69345427
0.6939119 0.45


In [22]:
# ,dkngld

# 0.6857662 # 0.68593323 : 0.47 TH
# 0.68798006  # 0.6884547 0.45
# 0.6903099 # 0.6911206 0.44
# 0.6909886 # 0.6928196 0.45



# 0.6914439 # 0.69235253 0.44


In [28]:
call_signs1 = [
#     "roh_01_tta", # can be removed
    "roh_02_tta",    
    "roh_04_tta", 
    "nir_01_tta",
#     "nir_05_tta", # remove this from ensemble
    "nir_06_tta",

    
    "121", 
    "122", 
    "125", 
    "127", 
    "131"  
] 

model_masks = torch.from_numpy(np.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/val_masks.npy")).flatten() 

preds = []

for idx, sign in tqdm(enumerate(call_signs1), total=len(call_signs1)):
    wt = torch.from_numpy(np.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/{sign}.npy")).flatten()   
    preds.append(wt)
    print(wt.shape)
    
    score = dice_coef(model_masks, wt, thr=0.5).cpu().detach().numpy() 
    print(score)
    
    
# # preds1.append(preds2)
    
final_preds = preds
# final_preds = torch.stack(final_preds).mean(dim=0)
# score = dice_coef(model_masks, final_preds, thr=0.5).cpu().detach().numpy() 

# print("0.5 TH Score: ", score)


# best_threshold = 0.0
# best_dice_score = 0.0
# for threshold in [i / 100 for i in range(101)] :
#     if threshold < 0.35 or threshold > 0.51:
#         continue
    
#     score = dice_coef(model_masks, final_preds, thr=threshold).cpu().detach().numpy() 
#     if score > best_dice_score:
#         best_dice_score = score
#         best_threshold = threshold
        
# print(best_dice_score, best_threshold)

  0%|          | 0/9 [00:00<?, ?it/s]

torch.Size([121634816])
0.67922837
torch.Size([121634816])
0.6797982
torch.Size([121634816])
0.6567023
torch.Size([121634816])
0.67292583
torch.Size([121634816])
0.6707117
torch.Size([121634816])
0.67332405
torch.Size([121634816])
0.65260977
torch.Size([121634816])
0.6755674
torch.Size([121634816])
0.6600541


In [29]:
def boost_dice(params, TH=None):    
    
    for index, val in enumerate(params.keys()):
        if index == 0:            
            preds = params[val]*final_preds[0]
        else:
            preds += params[val]*final_preds[index]
    
    param_sum = 0
    for key, val in params.items():
        param_sum += val

    preds = preds/param_sum
    
    
    if TH:
        best_threshold = TH
        preds1 = (preds).double()
        best_score = dice_coef(model_masks, preds1, thr=TH).cpu().detach().numpy() # get_score(labels, preds) 
    else:
        best_threshold = 0.0
        best_score = 0.0
        for threshold in [i / 100 for i in range(101)] :              
            if threshold < 0.3 or threshold > 0.65:
                continue

            preds1 = ((preds)>threshold).double()            
            score = dice_coef(model_masks, preds1, thr=threshold).cpu().detach().numpy() # get_score(labels, preds) 
            if score > best_score:
                best_score = score
                best_threshold = threshold
            
#     best_score = score
#     best_threshold = threshold
    return best_score, best_threshold

In [46]:
def objective(trial):
    TH = 0.41
    
    params = {}    
    for i in range(len(final_preds)):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1) 

        
    score, best_threshold  = boost_dice(params, TH=TH)
    params['threshold'] = best_threshold
    if not TH:
        print(params)
        
    return score

In [48]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1500)
best_params = study.best_params

[I 2023-07-16 20:27:12,270] A new study created in memory with name: no-name-b978d379-c56a-44a6-aeb6-54ffa76e9a17
[I 2023-07-16 20:27:13,396] Trial 0 finished with value: 0.6930090188980103 and parameters: {'w1': 0.264292439235295, 'w2': 0.8272040012637687, 'w3': 0.21451668037191085, 'w4': 0.6485399085097985, 'w5': 0.46368793986597456, 'w6': 0.6405951879084673, 'w7': 0.9232337584455688, 'w8': 0.6052441126695567, 'w9': 0.15015007612636722}. Best is trial 0 with value: 0.6930090188980103.
[I 2023-07-16 20:27:14,526] Trial 1 finished with value: 0.6930462718009949 and parameters: {'w1': 0.4886956534418254, 'w2': 0.7270996958066172, 'w3': 0.40010098151138374, 'w4': 0.8023673281030231, 'w5': 0.396179241721906, 'w6': 0.9619756103700723, 'w7': 0.595081012022386, 'w8': 0.12269285041817346, 'w9': 0.41711022591860003}. Best is trial 1 with value: 0.6930462718009949.
[I 2023-07-16 20:27:15,686] Trial 2 finished with value: 0.6906217932701111 and parameters: {'w1': 0.009815721466467808, 'w2': 0.75

[I 2023-07-16 20:27:39,293] Trial 22 finished with value: 0.6940599083900452 and parameters: {'w1': 0.5955880341098075, 'w2': 0.1816489838421133, 'w3': 0.5886420834459896, 'w4': 0.9805420330309504, 'w5': 0.5566980847659732, 'w6': 0.5764974996457821, 'w7': 0.6602919438703699, 'w8': 0.7073452249699239, 'w9': 0.23274313763780916}. Best is trial 20 with value: 0.6941477060317993.
[I 2023-07-16 20:27:40,457] Trial 23 finished with value: 0.6942685842514038 and parameters: {'w1': 0.5570056782734563, 'w2': 0.22413946228649334, 'w3': 0.4613205376608251, 'w4': 0.906303827254877, 'w5': 0.3034926562302121, 'w6': 0.43384936398108687, 'w7': 0.878131392462114, 'w8': 0.8289399089799013, 'w9': 0.1260772731493327}. Best is trial 23 with value: 0.6942685842514038.
[I 2023-07-16 20:27:41,663] Trial 24 finished with value: 0.6945006847381592 and parameters: {'w1': 0.5544169348986534, 'w2': 0.06990253761705198, 'w3': 0.446593989066295, 'w4': 0.9958971583751562, 'w5': 0.27271310046332825, 'w6': 0.4310789094

[I 2023-07-16 20:28:05,100] Trial 44 finished with value: 0.6944364905357361 and parameters: {'w1': 0.25997696174825613, 'w2': 0.24583910657145905, 'w3': 0.32645691192744974, 'w4': 0.794136900623317, 'w5': 0.271318969807932, 'w6': 0.28266450071245547, 'w7': 0.9590123740069332, 'w8': 0.731100177776487, 'w9': 0.157648995570546}. Best is trial 34 with value: 0.6946443915367126.
[I 2023-07-16 20:28:06,294] Trial 45 finished with value: 0.6942005157470703 and parameters: {'w1': 0.3346438995472991, 'w2': 0.047798882352948144, 'w3': 0.4084638505626589, 'w4': 0.6059679114316484, 'w5': 0.3333666946371018, 'w6': 0.08206340537378484, 'w7': 0.7296979574840313, 'w8': 0.7978226898470626, 'w9': 0.05742938233515097}. Best is trial 34 with value: 0.6946443915367126.
[I 2023-07-16 20:28:07,474] Trial 46 finished with value: 0.6947966814041138 and parameters: {'w1': 0.3949950871123535, 'w2': 0.09418648687469133, 'w3': 0.5477074408670812, 'w4': 0.6757315429768942, 'w5': 0.25568121369363483, 'w6': 0.238616

[I 2023-07-16 20:28:31,263] Trial 66 finished with value: 0.6950790882110596 and parameters: {'w1': 0.11344155430887037, 'w2': 0.33320766545423647, 'w3': 0.612143569355442, 'w4': 0.6179733233273726, 'w5': 0.10120781441402663, 'w6': 0.09167554726444804, 'w7': 0.4095612640996076, 'w8': 0.9436476601729252, 'w9': 0.3779827672011086}. Best is trial 56 with value: 0.6953450441360474.
[I 2023-07-16 20:28:32,429] Trial 67 finished with value: 0.695103645324707 and parameters: {'w1': 0.03290546219150866, 'w2': 0.3804166679620065, 'w3': 0.8228853942061525, 'w4': 0.6342989689420683, 'w5': 0.051316122339402616, 'w6': 0.15738885929135646, 'w7': 0.6438466325745177, 'w8': 0.9000327018634475, 'w9': 0.47443784684629187}. Best is trial 56 with value: 0.6953450441360474.
[I 2023-07-16 20:28:33,605] Trial 68 finished with value: 0.6951783895492554 and parameters: {'w1': 0.10071516331363867, 'w2': 0.3130087089495222, 'w3': 0.7493423071666714, 'w4': 0.5533402024190203, 'w5': 0.06393506301989219, 'w6': 0.041

[I 2023-07-16 20:28:57,350] Trial 88 finished with value: 0.6952983736991882 and parameters: {'w1': 0.2359634525243362, 'w2': 0.43715598855175986, 'w3': 0.6087766436792525, 'w4': 0.41405417581704346, 'w5': 0.16021388925248242, 'w6': 0.1687735702429105, 'w7': 0.5153495764981311, 'w8': 0.801344070909131, 'w9': 0.21878987238144765}. Best is trial 79 with value: 0.6954484581947327.
[I 2023-07-16 20:28:58,503] Trial 89 finished with value: 0.6952917575836182 and parameters: {'w1': 0.23306012808962218, 'w2': 0.44213589219299515, 'w3': 0.6292156011764721, 'w4': 0.4208489461070879, 'w5': 0.09376560827490167, 'w6': 0.19678522678631358, 'w7': 0.5515594881135172, 'w8': 0.7917264701530423, 'w9': 0.2065242970931223}. Best is trial 79 with value: 0.6954484581947327.
[I 2023-07-16 20:28:59,746] Trial 90 finished with value: 0.6951888203620911 and parameters: {'w1': 0.27939491542355976, 'w2': 0.5045264875464277, 'w3': 0.5702516773237705, 'w4': 0.4659446173779989, 'w5': 0.15945117660174588, 'w6': 0.169

...

[I 2023-07-16 20:57:00,461] Trial 1408 finished with value: 0.6925870180130005 and parameters: {'w1': 0.8163784864806167, 'w2': 0.5861061663900142, 'w3': 0.5829630298430717, 'w4': 0.06908815594837714, 'w5': 0.18599581783022057, 'w6': 0.08088181789662632, 'w7': 0.43967703925839635, 'w8': 0.8531402012384285, 'w9': 0.3671393882352325}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:57:01,733] Trial 1409 finished with value: 0.6939669251441956 and parameters: {'w1': 0.36388763389391043, 'w2': 0.8243400080704758, 'w3': 0.6204254420668859, 'w4': 0.4674229086359533, 'w5': 0.056578262290979425, 'w6': 0.5916385812176891, 'w7': 0.5346767751093257, 'w8': 0.9072518717226687, 'w9': 0.6225474653639866}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:57:03,067] Trial 1410 finished with value: 0.6948719024658203 and parameters: {'w1': 0.21537988559446153, 'w2': 0.5028616324661718, 'w3': 0.652431752890219, 'w4': 0.4237680029185029, 'w5': 0.2937951017605379, 'w6':

[I 2023-07-16 20:57:30,897] Trial 1430 finished with value: 0.6921096444129944 and parameters: {'w1': 0.06291154961965335, 'w2': 0.6416430099823061, 'w3': 0.23695392902821621, 'w4': 0.5372858237601824, 'w5': 0.6419251996748052, 'w6': 0.6418930918941683, 'w7': 0.2516339852616465, 'w8': 0.332658450718501, 'w9': 0.31778218249861384}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:57:32,242] Trial 1431 finished with value: 0.6943202018737793 and parameters: {'w1': 0.23008501760654262, 'w2': 0.4710882866780751, 'w3': 0.355253469970068, 'w4': 0.3490852640753525, 'w5': 0.14125106972390405, 'w6': 0.28419210854720267, 'w7': 0.5630206709099689, 'w8': 0.854435652575116, 'w9': 0.33230337356015205}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:57:33,630] Trial 1432 finished with value: 0.6933109164237976 and parameters: {'w1': 0.8655985472846166, 'w2': 0.4437057206589853, 'w3': 0.881280329418172, 'w4': 0.49858087589280464, 'w5': 0.699874449123275, 'w6': 0.1

[I 2023-07-16 20:58:00,950] Trial 1452 finished with value: 0.6946761012077332 and parameters: {'w1': 0.08923316886080813, 'w2': 0.4521963052079442, 'w3': 0.8850539631315354, 'w4': 0.6317770263814415, 'w5': 0.4692187612798896, 'w6': 0.13545449710556662, 'w7': 0.8228574304130476, 'w8': 0.8848466770214265, 'w9': 0.31058516196018293}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:58:02,260] Trial 1453 finished with value: 0.6926173567771912 and parameters: {'w1': 0.4989274188969204, 'w2': 0.9009024822559221, 'w3': 0.4617381263278204, 'w4': 0.1904515538512641, 'w5': 0.13402939681353337, 'w6': 0.10798472918717192, 'w7': 0.6408251790734214, 'w8': 0.791146489657443, 'w9': 0.2717789421760819}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:58:03,577] Trial 1454 finished with value: 0.6933832168579102 and parameters: {'w1': 0.11855001360621006, 'w2': 0.47766046934451445, 'w3': 0.6094510439051213, 'w4': 0.5433771697240783, 'w5': 0.21342721307597468, 'w6':

[I 2023-07-16 20:58:30,278] Trial 1474 finished with value: 0.6921660900115967 and parameters: {'w1': 0.06567422157793494, 'w2': 0.8026707381772714, 'w3': 0.42229818630125837, 'w4': 0.39972035590406196, 'w5': 0.07591291123263318, 'w6': 0.2150000095821626, 'w7': 0.493394913779865, 'w8': 0.09004109462490317, 'w9': 0.514641225837245}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:58:31,522] Trial 1475 finished with value: 0.6929696798324585 and parameters: {'w1': 0.38161195795734204, 'w2': 0.8323608023405491, 'w3': 0.56195104415891, 'w4': 0.49642194348282365, 'w5': 0.4079794934606492, 'w6': 0.08406110747680756, 'w7': 0.2893074357105934, 'w8': 0.6289223227699533, 'w9': 0.5569029949093922}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:58:32,824] Trial 1476 finished with value: 0.6935631036758423 and parameters: {'w1': 0.41892411941764374, 'w2': 0.4394851433642899, 'w3': 0.5443855385444639, 'w4': 0.22166794490604347, 'w5': 0.060662066180254576, 'w6'

[I 2023-07-16 20:58:59,852] Trial 1496 finished with value: 0.692593514919281 and parameters: {'w1': 0.72062031136909, 'w2': 0.5731709213687682, 'w3': 0.6190764142179677, 'w4': 0.5414577101825431, 'w5': 0.3237729601844326, 'w6': 0.13589514649944864, 'w7': 0.08586586205082836, 'w8': 0.9756996922364816, 'w9': 0.4056944142918147}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:59:01,212] Trial 1497 finished with value: 0.6894469261169434 and parameters: {'w1': 0.0662135162803344, 'w2': 0.06079646369636771, 'w3': 0.1745735876531891, 'w4': 0.1308440395189998, 'w5': 0.08192109129620484, 'w6': 0.157290560555297, 'w7': 0.39927699223199087, 'w8': 0.8815240806636536, 'w9': 0.24686145230255557}. Best is trial 133 with value: 0.6955258250236511.
[I 2023-07-16 20:59:02,573] Trial 1498 finished with value: 0.6938704252243042 and parameters: {'w1': 0.2843582860783314, 'w2': 0.4984696549338702, 'w3': 0.6007643578604416, 'w4': 0.7599950145154915, 'w5': 0.20748778692140515, 'w6': 0.7

In [49]:
len(final_preds) 

9

In [ ]:
# Trial 145 finished with value: 0.6954816579818726 and parameters: 
# {'w1': 0.3800712934060794, 'w2': 0.19827057881403873, 'w3': 0.8639190435791337, 'w4': 0.8183765509720466, 'w5': 0.17899313642679757, 'w6': 0.024590770644496746, 'w7': 0.7862484916619368, 'w8': 0.992834740398046, 'w9': 0.3995791428881191}. 
# Best is trial 145 with value: 0.6954816579818726. # 0.4

In [ ]:
# [I 2023-07-16 19:49:38,527] Trial 258 finished with value: 0.6955569982528687 and parameters: 
# {'w1': 0.35630544690551724, 'w2': 0.3882333167896021, 'w3': 0.793029020160463, 'w4': 0.589733873322586, 'w5': 0.1238533606039253, 'w6': 0.3136224869358406, 'w7': 0.7445672749651168, 'w8': 0.9585857088778065, 'w9': 0.3523881046014743}. Best is trial 258 with value: 0.6955569982528687.
# 0.41

In [ ]:
# [I 2023-07-16 20:01:35,463] Trial 231 finished with value: 0.6953996419906616 and parameters: {'w1': 0.03615687143100031, 'w2': 0.45224010503148204, 'w3': 0.663721473024527, 'w4': 0.6371224751418889, 'w5': 0.03698106916893698, 'w6': 0.15052361112796397, 'w7': 0.5701940304803765, 'w8': 0.910815487921195, 'w9': 0.47052561326641523}. Best is trial 231 with value: 0.6953996419906616.
# 0.42

In [ ]:
# 0.657336 0.01


# call_signs1 = [
#     "roh_01_tta", "nir_01_tta", "nir_02_tta", "nir_03_tta", "nir_04_tta"
# ] 

# call_signs1 = [
#     "roh_02_tta",  "roh_03_tta", "roh_04_tta", "roh_05_tta", "roh_06_tta",  "roh_07_tta",  "roh_08_tta"  
# ] 

call_signs1 = [
    "roh_01_tta",
    "roh_02_tta", 
    "roh_03_tta", 
    "nir_01_tta",
    "nir_02_tta",
    "nir_03_tta",
    "nir_04_tta",
    "121", 
    "122",
    "125", 
    "127",
    "131"
    
    
#     "ioa_01", 
#     "ioa_02",
#     "roh_02_tta"
    
] 

model_masks = torch.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/val_masks.pt")


preds1 = []

for idx, sign in tqdm(enumerate(call_signs1), total=len(call_signs1)):
    wt = torch.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/{sign}.pt")    
    preds1.append(wt)
    
    score = dice_coef(model_masks, wt, thr=0.5).cpu().detach().numpy() 
    print(score)
    
    
# preds1.append(preds2)
    
final_preds = preds1
final_preds = torch.stack(final_preds).mean(dim=0)
score = dice_coef(model_masks, final_preds, thr=0.5).cpu().detach().numpy() 

print("0.5 TH Score: ", score)


best_threshold = 0.0
best_dice_score = 0.0
for threshold in [i / 100 for i in range(101)] :
    score = dice_coef(model_masks, final_preds, thr=threshold).cpu().detach().numpy() 
    if score > best_dice_score:
        best_dice_score = score
        best_threshold = threshold
print(best_dice_score, best_threshold)

In [39]:
# 0.5 TH Score:  0.67887855
# 0.6856482 0.28



# 0.5 TH Score:  0.6811164
# 0.6867434 0.35


In [ ]:
def objective(trial):
    TH = None
    
    params = {}    
    for i in range(len(final_preds)):
        params[f"w{i+1}"] = trial.suggest_float(f'w{i+1}', 0, 1) 
        
    score, best_threshold  = boost_dice(params, TH=TH)
    params['threshold'] = best_threshold
    if not TH:
        print(params)
        
    return score

In [ ]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=1000)
best_params = study.best_params

In [34]:
call_signs1 = [
    "roh_01_tta_full", "nir_01_tta_full", "nir_02_tta_full", "nir_03_tta_full", "nir_04_tta_full"
] 

model_masks = torch.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/val_masks_full.pt")


preds1 = []

for idx, sign in tqdm(enumerate(call_signs1), total=len(call_signs1)):
    wt = torch.load(f"/home/rohits/pv1/Contrail_Detection/output/final_preds/{sign}.pt")    
    preds1.append(wt)
    
    score = dice_coef(model_masks, wt, thr=0.5).cpu().detach().numpy() 
    print(score)
    
final_preds = preds1
final_preds = torch.stack(final_preds).mean(dim=0)
score = dice_coef(model_masks, final_preds, thr=0.5).cpu().detach().numpy() 
print("0.5 TH Score: ", score)

best_threshold = 0.0
best_dice_score = 0.0
for threshold in [i / 100 for i in range(101)] :
    score = dice_coef(model_masks, final_preds, thr=threshold).cpu().detach().numpy() 
    if score > best_dice_score:
        best_dice_score = score
        best_threshold = threshold
print(best_dice_score, best_threshold)


  0%|          | 0/5 [00:00<?, ?it/s]

0.6469362
0.6567023
0.6457618
0.6704817
0.655622
0.5 TH Score:  0.6751985
0.6808599 0.35


In [ ]:
# 0.5 TH Score:  0.6760312
# 0.6810049 0.33

In [ ]:
# CFGS1 = [   
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'model_func': load_model_exp28,
#         'model_pth': '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#         'call_sign': "ioa_01",
#         'tta': True, #False, #True
#         'normalize': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "ioa_02",
#         'model_func': load_model_exp28_snapshot,
#         'tta': False, #True
#         'normalize': True,
#         'model_pth': [
#             ######## full train.csv 
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v2.ckpt',
#             ######### 4-skf split 
#         ]
#     }, 
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "roh_02",
#         'model_func': load_model_exp28_snapshot,        
#         'model_pth': '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#         'tta': False, #True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "roh_03",
#         'model_func': load_model_exp28_snapshot,        
#         'model_pth': '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v1.ckpt',
#         'tta': False, #True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "roh_04",
#         'model_func': load_model_exp28_snapshot,        
#         'model_pth': '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v2.ckpt',
#         'tta': False, #True
#     }, 
    
#         {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "ioa_02",
#         'model_func': load_model_exp28_snapshot,
#         'tta': False, #True
#         'normalize': True,
#         'model_pth': [
#             ######## full train.csv 
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v2.ckpt',
#             ######### 4-skf split 
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v1.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v2.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v3.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v4.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v5.ckpt'
#         ]
#     }, 
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'gluon_senet154',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'threshold': 0.5, #0.24,
#         'call_sign': "ioa_02_tta",
#         'model_func': load_model_exp28_snapshot,
#         'tta': True, #True
#         'normalize': True,
#         'model_pth': [
#             ######## full train.csv 
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v1.ckpt',
#             '/home/rohits/pv1/Contrail_Detection/output/ioannis/Unet-gluon_senet154_fold-1-v2.ckpt',
#             ######### 4-skf split 
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v1.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v2.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v3.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v4.ckpt',
#             #     '/kaggle/input/contrails-exp28b-senet154-512/Unet-gluon_senet154_fold0-v5.ckpt'
#         ]
#     }, 
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'efficientnet-b7',
#         'img_size': [256, 256],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/efficientnet-b7-256/checkpoint_dice_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_01_tta",
#         'model_func': load_modelr1,
#         'tta': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'efficientnet-b7',
#         'img_size': [256, 256],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/efficientnet-b7-256/checkpoint_dice_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_01",
#         'model_func': load_modelr1,
#         'tta': False
#     }, 
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'cs3darknet_l',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/cs3darknet_l-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_02_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
#         {
#         'model_name': 'Unet',
#         'backbone': 'cs3edgenet_x',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/cs3edgenet_x-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_03_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'cs3sedarknet_l',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/cs3sedarknet_l-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_04_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'ecaresnet101d',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/ecaresnet101d-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_05_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'ecaresnet269d',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/ecaresnet269d-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_06_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'fbnetv3_g',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/fbnetv3_g-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_07_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
        
#     {
#         'model_name': 'Unet',
#         'backbone': 'tf_mixnet_l',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/exp_01_s2/Unet/tf_mixnet_l-512/checkpoint_dice_ctrl_fold0.pth',
#         'threshold': 0.24, #0.24,
#         'call_sign': "roh_08_tta",
#         'model_func': load_modelr2,
#         'tta': True
#     }, 
    
    

#     {
#         'model_name': 'Unet',
#         'backbone': 'maxvit_small_tf_512',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/maxvitfold0mix_maxvit_small_tf_512_best_epochstage2oof685cv657-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_01_tta",
#         'model_func': load_model4,
#         'tta': True
#     },
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'eca_nfnet_l1',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl1v2fold0_eca_nfnet_l1_best_epochstage2-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_02_tta",
#         'model_func': load_model2,
#         'tta': True
#     },
#     {
#         'model_name': 'Unet++',
#         'backbone': 'tf_efficientnet_b8',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/effb8modelv2fold0_tf_efficientnet_b8_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_03_tta", 
#         'model_func': load_model3,
#         'tta': True
#     },
#     {
#         'model_name': 'Unet++',
#         'backbone': 'tf_efficientnet_b7_ns',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/contrail_01/output/nirjhar/qishentrialv2fpn512_tf_efficientnet_b7_ns_best_epochcv650lb675-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_04_tta", 
#         'model_func': load_model1,
#         'tta': True
#     }, 
    
    
    
#         {
#         'model_name': 'Unet',
#         'backbone': 'eca_nfnet_l2',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl2v2fold0_eca_nfnet_l2_best_epochstage2-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_05_tta",
#         'model_func': load_model2,
#         'tta': True
#     },
#     {
#     'model_name': 'Unet++',
#         'backbone': 'densenetblur121d',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl2v2fold0_densenetblur121d_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_06_tta", 
#         'model_func': load_model2,
#         'tta': True
#     },
    
#     {
#     'model_name': 'Unet++',
#         'backbone': 'convnextv2_base',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/convnextfold0_convnextv2_base_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_07_tta", 
#         'model_func': load_model2,
#         'tta': True
#     },
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'maxvit_small_tf_512',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/maxvitfold0mix_maxvit_small_tf_512_best_epochstage2oof685cv657-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_01",
#         'model_func': load_model4,
#         'tta': False
#     },
    
    
#     {
#         'model_name': 'Unet',
#         'backbone': 'eca_nfnet_l1',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl1v2fold0_eca_nfnet_l1_best_epochstage2-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_02",
#         'model_func': load_model2,
#         'tta': False
#     },
#     {
#         'model_name': 'Unet++',
#         'backbone': 'tf_efficientnet_b8',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/effb8modelv2fold0_tf_efficientnet_b8_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_03", 
#         'model_func': load_model3,
#         'tta': False
#     },
#     {
#         'model_name': 'Unet++',
#         'backbone': 'tf_efficientnet_b7_ns',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/contrail_01/output/nirjhar/qishentrialv2fpn512_tf_efficientnet_b7_ns_best_epochcv650lb675-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_04", 
#         'model_func': load_model1,
#         'tta': False
#     }, 
    
#         {
#         'model_name': 'Unet',
#         'backbone': 'eca_nfnet_l2',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl2v2fold0_eca_nfnet_l2_best_epochstage2-00.bin',
#         'threshold': 0.62, #0.24,
#         'call_sign': "nir_05",
#         'model_func': load_model2,
#         'tta': False
#     },
#     {
#     'model_name': 'Unet++',
#         'backbone': 'densenetblur121d',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/ecanfnetl2v2fold0_densenetblur121d_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_06", 
#         'model_func': load_model2,
#         'tta': False
#     },
    
#     {
#     'model_name': 'Unet++',
#         'backbone': 'convnextv2_base',
#         'img_size': [512, 512],
#         'num_classes': 1,
#         'model_pth':  '/home/rohits/pv1/Contrail_Detection/output/nirjhar/convnextfold0_convnextv2_base_best_epochstage2-00.bin',
#         'threshold': 0.79,
#         'call_sign': "nir_07", 
#         'model_func': load_model2,
#         'tta': False
#     },
    
    
    
    
    
# ]